# Copying Adam Taylor's PCam5c driver to python top layer

In [1]:
from pynq import Overlay
from kv260 import BaseOverlay
from pynq.lib.iic import AxiIIC 
from pynq.lib.video import *
import numpy as np
from time import sleep

#base = BaseOverlay("base_tweaks/base_v0.bit", ignore_version=True)
adams = Overlay("adam_taylor/taylor_v1.bit", ignore_version=True)

#adams = Overlay("/kv260/video/base.bit", ignore_version=True)

I am in the pcam5c.py file now


In [2]:
adams?

In [3]:
iic = adams.axi_iic_0

iic_cam_addr = 0x3c
sw_iic_addr = 0x74
rx_data = bytes(10)
tx_data = [0,0,0,0,0,0]

In [4]:
def setup_i2c_switch():
    tx_data[0] = 0x04

    iic.send(sw_iic_addr, tx_data, 1)               

In [5]:
def detect_camera():
    tx_data[0] = 0x31;  tx_data[1] = 0x00;

    iic.send(iic_cam_addr, tx_data, 2)        
    print('send complete')
    sleep(0.5)
    
    status = iic.receive(iic_cam_addr, rx_data, 1)
    if hex(rx_data[0]) != '0x78':
        print("camera not detected")
        print(rx_data)        
    else:
        print("camera detected")            

In [6]:
def reset_camera(cfg):   
    tx_data[0] = 0x30; tx_data[1] = 0x08; tx_data[2] = cfg;
    
    iic.send(iic_cam_addr, tx_data, 3)          

In [7]:
def camera_chip_id_low():   
    tx_data[0] = 0x30;  tx_data[1] = 0x0A;

    iic.send(iic_cam_addr, tx_data, 2)               
    status = iic.receive(iic_cam_addr, rx_data, 1)

    if hex(rx_data[0]) != '0x56':
        print("Read fail at register 300A ")
    else:
        print("register 300A read correct")

In [8]:
def camera_chip_id_high():    
    tx_data[0] = 0x30;  tx_data[1] = 0x0B;

    iic.send(iic_cam_addr,tx_data,2)               
    status = iic.receive(iic_cam_addr, rx_data, 1)

    if hex(rx_data[0]) != '0x40':
        print("Read fail at register 300A ")
    else:
        print("register 300A read correct")

In [9]:
def camera_system_clk(): 
    tx_data[0] = 0x31;  tx_data[1] = 0x03;
    tx_data[2] = 0x11

    iic.send(iic_cam_addr, tx_data, 3) 

In [10]:
def iic_tx(reg, val):
    tx_data[0] = (reg>>8) & (0xFF);
    tx_data[1] = reg & (0xFF);
    tx_data[2] = val
    
    iic.send(iic_cam_addr, tx_data, 3) 
    print("sent -> {} {} {}".format(hex(tx_data[0]),hex(tx_data[1]),hex(tx_data[2])))

In [11]:
setup_i2c_switch()

In [12]:
detect_camera()

send complete
camera detected


In [13]:
camera_chip_id_low()

register 300A read correct


In [14]:
camera_chip_id_high()

register 300A read correct


In [15]:
camera_system_clk()

In [16]:
iic_tx(0x3008, 0x82)

sent -> 0x30 0x8 0x82


In [17]:
detect_camera()

send complete
camera detected


In [18]:
iic_tx(0x3008, 0x02)

sent -> 0x30 0x8 0x2


In [19]:
detect_camera()

send complete
camera detected


In [20]:
iic_tx(0x3008, 0x42)

sent -> 0x30 0x8 0x42


In [21]:
detect_camera()

send complete
camera detected


In [22]:
iic_tx(0x3008, 0x82)

sent -> 0x30 0x8 0x82


In [ ]:
detect_camera()

In [ ]:
iic_tx(0x3008, 0x02)

In [ ]:
detect_camera()

In [ ]:
from pynq import DefaultIP

class Demosaic(DefaultIP):
    def __init__(self,description):
        super().__init__(description=description)
        
    bindto = ['xilinx.com:hls:demosaic:1.0']
    
    def config(self, width, height):
        demosaic.write(0x10, width)
        demosaic.write(0x18, height)
        demosaic.write(0x20, 0)
        demosaic.write(0x28, 0)
        demosaic.write(0x00, 81)
        return 

In [ ]:
mipi = adams.mipi_csi2_rx_subsyst_0
mipi?

In [ ]:
demosaic = adams.v_demosaic_0
demosaic.write(0x10, 1280)
demosaic.write(0x18, 720)
demosaic.write(0x20, 0)
demosaic.write(0x28, 0)
demosaic.write(0x00, 81)
demosaic?

In [ ]:
gamma = adams.v_gamma_lut_0
gamma?

In [ ]:
iic = adams.axi_iic_0
iic?

Defining key addresses

In [ ]:
cam_id = 0x78
iic_cam_addr = 0x3c
sw_iic_addr = 0x74

rx_data = bytes(10)
tx_data = [0,0,0,0,0,0]

Setting the I2C switch

In [ ]:
tx_data[0] = 0x04

iic.send(sw_iic_addr,tx_data,1)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(sw_iic_addr, rx_data, 1)

print(status)

# Function to detect the camera - reading the ID

In [ ]:
def detect_camera():
    
    tx_data = [0,0,0,0,0]
    tx_data[0] = 0x31;  tx_data[1] = 0x00;

    iic.send(iic_cam_addr,tx_data,2)               # send(address,data,length of data, "option" - not necessary)
    print('send complete')
    sleep(0.5)
    status = iic.receive(iic_cam_addr, rx_data, 1)

    if hex(rx_data[0]) != '0x78':
        print("camera not detected")
        print(rx_data)
        
    else:
        print("camera detected")

In [ ]:
detect_camera()

Includinmg a section that writes to the CAM_PWUP (cam_gpio) pin as outlined in step one of power up:

note: adam taylor doesn't need this

In [ ]:
'''Keeping this here but ommiting from run as adam taylor doesnt'''

#note remember the wait for 50ms

# Execute a power-cycle by applying a low pulse of 100ms on CAM_PWUP, then driving it high - writing to cam_gpio 
#adams.gpio_ip_reset[0].write(0) 
#sleep(1)
#adams.gpio_ip_reset[0].write(1) 

Register check for sanity as outlined in step 3 of guide

note: Adam Taylor also doesn't do this

In [ ]:
tx_data[0] = 0x30;  tx_data[1] = 0x0A;

iic.send(iic_cam_addr,tx_data,2)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)

if hex(rx_data[0]) != '0x56':
  print("Read fail at register 300A ")
else:
    print("register 300A read correct")

tx_data[0] = 0x30;  tx_data[1] = 0x0B;

iic.send(iic_cam_addr,tx_data,2)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)

if hex(rx_data[0]) != '0x40':
  print("Read fail at register 300A ")
else:
  print("register 300A read correct")

Step 4 on guide - choosing input clock by writing 0x11 to register address 0x3103.

In [ ]:
tx_data[0] = 0x31;  tx_data[1] = 0x03;
tx_data[2] = 0x11

iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)

print(hex(rx_data[0]))

Step 5 Execute software reset by writing 0x82 to register address 0x3008.

In [ ]:
tx_data[0] = 0x30;  tx_data[1] = 0x08;
tx_data[2] = 0x82

iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)
status = iic.receive(iic_cam_addr, rx_data, 1)
#print(hex(rx_data[0]))

In [ ]:
sleep(1)   # Digilent guide says sleep for 10ms - adam taylor does 1s and his works 

Reaching out to the *cfg_init* structure for the following steps of the guide:


In [ ]:
#array and function for extracting and writing the addresses stored here are in the pcam_cfg.py file

%run pcam_cfg.ipynb

In [ ]:
#Sending commands to the addresses as part of the cfg_init library - bulletpoints 6-8 of digi guide
setting_func(cfg_init)

#setting the desired frame rate configurations 
setting_func(cfg_720p_60fps)

print('configuration complete')

In [ ]:
'''
#EXECUTE SOFTWARE RESET
tx_data[0] = 0x30;  tx_data[1] = 0x08;
tx_data[2] = 0x02

iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)

sleep(0.01)'''

In [ ]:
#EXECUTE SOFTWARE RESET
tx_data[0] = 0x30;  tx_data[1] = 0x08;
tx_data[2] = 0x42

iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)


In [ ]:
setting_func(cfg_simple_awb)

Set up Video Timing controller 

In [ ]:
videomode = VideoMode(1280,720,24)

#vdma.readchannel.stop()
#vdma.readchannel.mode = videomode

In [ ]:
videomode?

Here Adam taylor configures the VDMA block - does this have to be done in my case? Beyond what I am doing below 

In [ ]:
vdma.readchannel.start()

Repeating functions for camera detection and resets

In [ ]:
detect_camera()

#choose system input clock from pad
tx_data[0] = 0x31;  tx_data[1] = 0x03;
tx_data[2] = 0x11

iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)

#EXECUTE SOFTWARE RESET
#tx_data[0] = 0x30;  tx_data[1] = 0x08;
#tx_data[2] = 0x82

#iic.send(iic_cam_addr,tx_data,3)               # send(address,data,length of data, "option" - not necessary)

sleep(1)

Adam Taylor then resends the commands to read through all three configuration files

In [ ]:
#Sending commands to the addresses as part of the cfg_init library - bulletpoints 6-8 of digi guide
setting_func(cfg_init)

setting_func(cfg_simple_awb)

#setting the desired frame rate configurations 
setting_func(cfg_720p_60fps)

print('configuration complete')

In [ ]:
vdma.readchannel.start()

Adam Taylor then starts his vdma block by writing to it 

In [ ]:
frame = vdma.readchannel.readframe()